In [18]:
import billboard as bl
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials

import spotipy.util

import pandas as pd 
import numpy as np
import yt_dlp

#chart = bl.ChartData('hot-100')




# 1. Collect Data

In [19]:
chartData = pd.DataFrame(columns=['Titles', 'Artist', 'Popularity'])

chart=[]
title = []
artist = []
rank = []
for y in range(2022, 2017, -1):
    chart = bl.ChartData('hot-100-songs', year=y)
    for entry in chart.entries:
        title.append(entry.title)
        artist.append(entry.artist)
        

    
chartData['Titles'] = title
chartData['Artist'] = artist


chartData['Popularity'] = 1

                 


chartData

Titles                                      Artist  Popularity
0         Heat Waves                               Glass Animals           1
1          As It Was                                Harry Styles           1
2               Stay               The Kid LAROI & Justin Bieber           1
3         Easy On Me                                       Adele           1
4            Shivers                                  Ed Sheeran           1
..               ...                                         ...         ...
495  One Number Away                                  Luke Combs           1
496       Powerglide                      Rae Sremmurd & Juicy J           1
497            IDGAF                                    Dua Lipa           1
498         Mi Gente  J Balvin & Willy William Featuring Beyonce           1
499         Believer                             Imagine Dragons           1

[500 rows x 3 columns]

In [20]:
client_id = '4369430b36ce4847ab0a39d5aea1c29d'
client_secret = 'ff8d1dd250e64346b04f790b08459f8f'
client_credentials_manager = SpotifyClientCredentials(client_id=client_id, client_secret=client_secret)
sp = spotipy.Spotify(client_credentials_manager=client_credentials_manager)

In [21]:
for artist in chartData['Artist'].unique():
    results = sp.search(q='artist:' + artist, type='track', limit=10)
    songs = results['tracks']['items']
    all_songs = [song['name'] for song in songs if '2018-01-01' <= song['album']['release_date'] <= '2022-12-31']
    all_songs=set(all_songs)
    filteredsongs=[]
    for song in all_songs:
        if song not in chartData['Titles'].values:
            filteredsongs.append(song)
    for song in filteredsongs:
        row={'Titles': song, 'Artist':artist, 'Popularity':0}
        chartData.loc[len(chartData)] = row

chartData

Titles                         Artist  Popularity
0                  Heat Waves                  Glass Animals           1
1                   As It Was                   Harry Styles           1
2                        Stay  The Kid LAROI & Justin Bieber           1
3                  Easy On Me                          Adele           1
4                     Shivers                     Ed Sheeran           1
...                       ...                            ...         ...
1221                    Catch                    Brett Young           0
1222             Here Tonight                    Brett Young           0
1223                     Lady                    Brett Young           0
1224               You Didn’t                    Brett Young           0
1225  Powerglide - From SR3MM         Rae Sremmurd & Juicy J           0

[1226 rows x 3 columns]

In [22]:
chartData.Artist.value_counts()

Artist
Olivia Rodrigo                                14
Ariana Grande                                 13
Drake                                         13
Lil Baby                                      12
Luke Combs                                    12
                                              ..
Ariana Grande & Justin Bieber                  1
Pop Smoke Featuring Lil Tjay                   1
BENEE Featuring Gus Dapperton                  1
THE SCOTTS, Travis Scott & Kid Cudi            1
J Balvin & Willy William Featuring Beyonce     1
Name: count, Length: 325, dtype: int64

In [23]:
chartData.drop_duplicates()

chartData

Titles                         Artist  Popularity
0                  Heat Waves                  Glass Animals           1
1                   As It Was                   Harry Styles           1
2                        Stay  The Kid LAROI & Justin Bieber           1
3                  Easy On Me                          Adele           1
4                     Shivers                     Ed Sheeran           1
...                       ...                            ...         ...
1221                    Catch                    Brett Young           0
1222             Here Tonight                    Brett Young           0
1223                     Lady                    Brett Young           0
1224               You Didn’t                    Brett Young           0
1225  Powerglide - From SR3MM         Rae Sremmurd & Juicy J           0

[1226 rows x 3 columns]

# 2. Download the full songs from Youtube using youtube-dl.

In [24]:
import yt_dlp
import os

def download_song(song_name, artist_name):
    search_query = f'{song_name} {artist_name} audio'
    output_file = os.path.join("P:\youtube-dl\songs", f'{song_name}.mp3')

    # Check if the file already exists
    if os.path.exists(output_file):
        print(f'{song_name} {artist_name} already downloaded. Skipping...')
        return

    ydl_opts = {
        'default_search': f'ytsearch:{search_query}',
        'format': 'bestaudio/best',
        'postprocessors': [{
            'key': 'FFmpegExtractAudio',
            'preferredcodec': 'mp3',
            'preferredquality': '192',
        }],
        'postprocessor_args': [
            '-ar', '44100'
        ],
        'prefer_ffmpeg': True,
        'noplaylist': True,
        'nocheckcertificate': True,
        'quiet': True,
        'outtmpl': output_file,
        'audioformat': "mp3",
        'ffmpeg_location': 'P:/youtube-dl/ffmpeg-6.0-full_build/bin'
    }

    try:
        with yt_dlp.YoutubeDL(ydl_opts) as ydl:
            ydl.download([search_query])
        print(f'{song_name} {artist_name} downloaded successfully.')
    except Exception as e:
        print(f'Error occurred while downloading {song_name} {artist_name}: {str(e)}')

In [25]:
# for t, n in zip(chartData['Titles'], chartData['Artist']):
#     download_song(t, n)

In [26]:
chartData.drop(chartData[chartData['Titles'] == '528 Hz Release Inner Conflict & Struggle.mp3.mp3'].index)
chartData.drop(chartData[chartData['Titles'] == '7 Hz Meditation & Inner Peace - Binaural Beats.mp3'].index)
chartData.drop(chartData[chartData['Titles'] == '963 Hz Courage & Inner Power'].index)
chartData.drop(chartData[chartData['Titles'] == 'Good Night Baby Shark'].index)
chartData.drop(chartData[chartData['Titles'] == 'PRACTICE'].index)

chartData

Titles                         Artist  Popularity
0                  Heat Waves                  Glass Animals           1
1                   As It Was                   Harry Styles           1
2                        Stay  The Kid LAROI & Justin Bieber           1
3                  Easy On Me                          Adele           1
4                     Shivers                     Ed Sheeran           1
...                       ...                            ...         ...
1221                    Catch                    Brett Young           0
1222             Here Tonight                    Brett Young           0
1223                     Lady                    Brett Young           0
1224               You Didn’t                    Brett Young           0
1225  Powerglide - From SR3MM         Rae Sremmurd & Juicy J           0

[1226 rows x 3 columns]

# 3. Extract the repeated chorus using pychorus.

In [27]:
import os
import time
from pychorus import find_and_output_chorus

# Define the paths to the songs folder and the output folder
songs_folder = "P:\youtube-dl\songs"
output_folder = "P:\youtube-dl\chorus"
max_processing_time = 60  # Maximum processing time in seconds for each song

# Define a modified version of find_and_output_chorus that includes elapsed time check
def find_and_output_chorus_with_time_limit(input_file, output_file, clip_length=15, max_time=60):
    if os.path.exists(output_file):
        print('already Procecced. Skipping...')
        return
    start_time = time.time()  # Start the timer
    find_and_output_chorus(input_file, output_file, clip_length)  # Extract the chorus
    elapsed_time = time.time() - start_time  # Calculate the elapsed time


    if elapsed_time > max_time:
        os.remove(output_file)  # Remove the output file if it took too long
        print(f"Skipping {os.path.basename(input_file)} due to long processing time ({elapsed_time} seconds)")
    else:
        print(f"Chorus extracted from {os.path.basename(input_file)} and saved as {os.path.basename(output_file)}")

# #Iterate over each file in the songs folder
# for filename in os.listdir(songs_folder):
#     if filename.endswith(".mp3"):  # Assuming the songs are in MP3 format
#         song_path = os.path.join(songs_folder, filename)
#         output_path = os.path.join(output_folder, f"{os.path.splitext(filename)[0]}.chorus.wav")

#         print(f"Processing {os.path.basename(song_path)}...")

#         # Use the modified find_and_output_chorus function with the maximum processing time
#         find_and_output_chorus_with_time_limit(song_path, output_path, 15, max_processing_time)


# 4. Extract the audio features of the hooks using Librosa

In [28]:
# chartData['chroma_stft']=None
# chartData['chroma_cqt']=None
# chartData['chroma_cens']=None
# chartData['mfcc']=None
# chartData['rms']=None
# chartData['spectral_centroid']=None
# chartData['spectral_bandwidth']=None
# chartData['spectral_contrast']=None
# chartData['spectral_rolloff']=None
# chartData['tonnetz']=None
# chartData['zero_crossing_rate']=None


In [29]:
# import os
# import librosa


# # Create a new DataFrame to store the valid rows
# validChartData = pd.DataFrame(columns=chartData.columns)

# for index, row in chartData.iterrows():
#     audio_file = f"P:/youtube-dl/chorus/{row.Titles}.chorus.wav"
    
#     # Check if the audio file exists
#     if os.path.exists(audio_file):
#         try:
#             y, sr = librosa.load(audio_file)
#             row['chroma_stft'] = librosa.feature.chroma_stft(y=y, sr=sr)
#             row['mfcc'] = librosa.feature.mfcc(y=y, sr=sr)
#             row['rms'] = np.sqrt(np.mean(y**2))
#             row['spectral_centroid'] = librosa.feature.spectral_centroid(y=y, sr=sr)
#             row['spectral_bandwidth'] = librosa.feature.spectral_bandwidth(y=y, sr=sr)
#             row['spectral_contrast'] = librosa.feature.spectral_contrast(y=y, sr=sr)
#             row['spectral_rolloff'] = librosa.feature.spectral_rolloff(y=y, sr=sr)
#             row['tonnetz'] = librosa.feature.tonnetz(y=y, sr=sr)
#             row['zero_crossing_rate'] = librosa.feature.zero_crossing_rate(y)
#             row['chroma_cqt'] = librosa.feature.chroma_cqt(y=y, sr=sr)
#             row['chroma_cens'] = librosa.feature.chroma_cens(y=y, sr=sr)
#             #print(row)
#             # Append the valid row to the new DataFrame
#             #validChartData = validChartData.concate(row)
            
#             print(f"Audio features Extracted: {audio_file}")
#             # validChartData = pd.concat([validChartData, pd.DataFrame(row)], ignore_index=True)
#             validChartData.loc[len(validChartData)] = row

#             # Using the at indexer
#             row_index = len(validChartData)
#             for column_name, value in row.items():
#                 validChartData.at[row_index, column_name] = value
            
#             #validChartData.iloc[len(validChartData)] = row
            
            
#             #print(validChartData)
#         except Exception as e:
#             print(f"Error processing audio file: {audio_file}")
#             print(e)
#     else:
#         print(f"Audio file not found: {audio_file}")

# # Update chartData with the valid rows
# chartData = validChartData


In [30]:
import librosa
import numpy as np
import scipy
from scipy.stats import skew, kurtosis
features=['chroma_stft','chroma_cqt','chroma_cens','mfcc','spectral_centroid','spectral_bandwidth','spectral_rolloff','tonnetz','spectral_contrast']
features2=['rms','zero_crossing_rate']

validChartData = pd.DataFrame(columns=chartData.columns)
# Create a new row for each iteration
new_row = {}


for index, row in chartData.iterrows():
    audio_file = f"P:/youtube-dl/chorus/{row.Titles}.chorus.wav"
    new_row['Titles'] = row['Titles']  # Assuming 'Titles' is one of the columns in chartData
    new_row['Artist'] = row['Artist']  # Assuming 'Titles' is one of the columns in chartData
    new_row['Popularity'] = row['Popularity']                    
    if os.path.exists(audio_file):
        try:
            y, sr = librosa.load(audio_file)
            for feature in features:
                feature_array = getattr(librosa.feature, feature)(y=y)
                for index2 in range(0, feature_array.shape[0]):
                    new_row[f'{feature}{index2}min'] = np.min(feature_array[index2])
                    new_row[f'{feature}{index2}mean'] = np.mean(feature_array[index2])
                    new_row[f'{feature}{index2}median'] = np.median(feature_array[index2])
                    new_row[f'{feature}{index2}max'] = np.max(feature_array[index2])
                    new_row[f'{feature}{index2}std'] = np.std(feature_array[index2])
                    new_row[f'{feature}{index2}skew'] = skew(feature_array[index2])
                    new_row[f'{feature}{index2}kurtosis'] = kurtosis(feature_array[index2])

                    # Append the new row to validChartData
                    row_index = len(validChartData)
                    for column_name, value in new_row.items():
                        validChartData.at[row_index, column_name] = value

            print(f"Audio features [1] Extracted: {audio_file}")
            for feature2 in features2:
                feature_array = getattr(librosa.feature, feature2)(y=y)
                for index2 in range(0,feature_array.shape[0]):
                    new_row[f'{feature}{index2}mean']=np.mean(feature_array[index2])
                    new_row[f'{feature}{index2}median']=np.median(feature_array[index2])
                    new_row[f'{feature}{index2}max']=np.max(feature_array[index2])
                    new_row[f'{feature}{index2}std']=np.std(feature_array[index2])
                    new_row[f'{feature}{index2}skew']=skew(feature_array[index2])
                    new_row[f'{feature}{index2}kurtosis']=kurtosis(feature_array[index2])
                    
                    row_index = len(validChartData)
                    for column_name, value in new_row.items():
                        validChartData.at[row_index, column_name] = value

                    # Using the at indexer
                    
            print(f"Audio features [2] Extracted: {audio_file}")
        
        except Exception as e:
            print(f"Error processing audio file: {audio_file}")
            print(e)
    else:
        print(f"Audio file not found: {audio_file}")

 



chartData = validChartData
        

Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/

C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  validChartData.at[row_index, column_name] = value
C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  validChartData.at[row_index, column_name] = value
C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times,

Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/

C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  validChartData.at[row_index, column_name] = value
C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  validChartData.at[row_index, column_name] = value
C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:35: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times,

Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav


...

Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [2] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [2] Extracted: P:/youtube-dl/chorus/Heat Waves.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/As It Was.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/As It Was.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/As It Was.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/As It Was.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/As It Was.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/As It

C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:29: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  new_row[f'{feature}{index2}skew'] = skew(feature_array[index2])
C:\Users\George Saeid\AppData\Local\Temp\ipykernel_27896\3036295835.py:30: RuntimeWarning: Precision loss occurred in moment calculation due to catastrophic cancellation. This occurs when the data are nearly identical. Results may be unreliable.
  new_row[f'{feature}{index2}kurtosis'] = kurtosis(feature_array[index2])


Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/MotorSport.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/

p:\Technocolabs Project\Building-a-Model-to-Predict-Hit-Songs-Using-Repeated-Chorus\chorus_env\Lib\site-packages\librosa\core\pitch.py:102: UserWarning: Trying to estimate tuning from empty frequency set.
  return pitch_tuning(


Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio features [1] Extracted: P:/youtube-dl/chorus/Bartier Cardi.chorus.wav
Audio featur

# The Final Dataset

In [31]:
chartData.drop_duplicates(subset=['Titles'], inplace=True)
chartData

Titles                             Artist Popularity  \
0             Heat Waves                      Glass Animals          1   
74             As It Was                       Harry Styles          1   
148                 Stay      The Kid LAROI & Justin Bieber          1   
222           Easy On Me                              Adele          1   
296              Shivers                         Ed Sheeran          1   
...                  ...                                ...        ...   
61420  Murder on My Mind                          YNW Melly          0   
61494        Meant to Be  Bebe Rexha & Florida Georgia Line          0   
61568               SAD!                       XXXTENTACION          0   
61642  Never Be the Same                     Camila Cabello          0   
61716            FRIENDS            Marshmello & Anne-Marie          0   

       chroma_stft0min  chroma_stft0mean  chroma_stft0median  chroma_stft0max  \
0             0.059570          0.545834            0.533472              1.0   
74            0.015278          0.275439            0.220617              1.0   
148           0.003053          0.404523            0.303565              1.0   
222           0.022964          0.520446            0.448787              1.0   
296           0.011913          0.306369            0.248468              1.0   
...                ...               ...                 ...              ...   
61420         0.023746          0.701988            0.804352              1.0   
61494         0.010370          0.529302            0.495058              1.0   
61568         0.007010          0.446956            0.389904              1.0   
61642         0.018414          0.531474            0.474381              1.0   
61716         0.002317          0.548961            0.501965              1.0   

       chroma_stft0std  chroma_stft0skew  chroma_stft0kurtosis  ...  \
0             0.256343          0.083067             -1.076719  ...   
74            0.227223          1.421183              1.736252  ...   
148           0.318527          0.687616             -0.836719  ...   
222           0.363114          0.184452             -1.552734  ...   
296           0.234462          1.032351              0.457811  ...   
...                ...               ...                   ...  ...   
61420         0.312264         -0.518006             -1.213881  ...   
61494         0.324113          0.124332             -1.287047  ...   
61568         0.296496          0.397012             -0.994168  ...   
61642         0.347591          0.179811             -1.491496  ...   
61716         0.366380          0.027494             -1.577043  ...   

       spectral_contrast5std  spectral_contrast5skew  \
0                        NaN                     NaN   
74                  2.087949                0.468411   
148                 2.639605                1.039552   
222                 3.572077                0.140919   
296                 4.424209                0.036302   
...                      ...                     ...   
61420               2.544686                0.121852   
61494               4.593361                0.448705   
61568               2.776943                0.127441   
61642               2.663166                0.560173   
61716               3.946151                0.225784   

       spectral_contrast5kurtosis  spectral_contrast6min  \
0                             NaN                    NaN   
74                       0.584898              10.197961   
148                      1.358847              12.225095   
222                     -0.726412              14.191255   
296                     -0.939122               9.195723   
...                           ...                    ...   
61420                   -0.175505              14.525187   
61494                   -0.977389              12.194958   
61568                   -0.509352              17.414860   
61642                    0.123

In [35]:
chartData.to_csv(r'P:\youtube-dl\Final_Features_Data.csv')

p:\Technocolabs Project\Building-a-Model-to-Predict-Hit-Songs-Using-Repeated-Chorus\chorus_env\Lib\site-packages\pandas\core\internals\blocks.py:2538: RuntimeWarning: invalid value encountered in cast
  values = values.astype(str)


In [34]:
chartData.isnull().sum()

Titles                        0
Artist                        0
Popularity                    0
chroma_stft0min               0
chroma_stft0mean              0
                             ..
spectral_contrast6median      1
spectral_contrast6max         1
spectral_contrast6std         1
spectral_contrast6skew        1
spectral_contrast6kurtosis    1
Length: 507, dtype: int64

In [36]:
chartData

Titles                             Artist Popularity  \
0             Heat Waves                      Glass Animals          1   
74             As It Was                       Harry Styles          1   
148                 Stay      The Kid LAROI & Justin Bieber          1   
222           Easy On Me                              Adele          1   
296              Shivers                         Ed Sheeran          1   
...                  ...                                ...        ...   
61420  Murder on My Mind                          YNW Melly          0   
61494        Meant to Be  Bebe Rexha & Florida Georgia Line          0   
61568               SAD!                       XXXTENTACION          0   
61642  Never Be the Same                     Camila Cabello          0   
61716            FRIENDS            Marshmello & Anne-Marie          0   

       chroma_stft0min  chroma_stft0mean  chroma_stft0median  chroma_stft0max  \
0             0.059570          0.545834            0.533472              1.0   
74            0.015278          0.275439            0.220617              1.0   
148           0.003053          0.404523            0.303565              1.0   
222           0.022964          0.520446            0.448787              1.0   
296           0.011913          0.306369            0.248468              1.0   
...                ...               ...                 ...              ...   
61420         0.023746          0.701988            0.804352              1.0   
61494         0.010370          0.529302            0.495058              1.0   
61568         0.007010          0.446956            0.389904              1.0   
61642         0.018414          0.531474            0.474381              1.0   
61716         0.002317          0.548961            0.501965              1.0   

       chroma_stft0std  chroma_stft0skew  chroma_stft0kurtosis  ...  \
0             0.256343          0.083067             -1.076719  ...   
74            0.227223          1.421183              1.736252  ...   
148           0.318527          0.687616             -0.836719  ...   
222           0.363114          0.184452             -1.552734  ...   
296           0.234462          1.032351              0.457811  ...   
...                ...               ...                   ...  ...   
61420         0.312264         -0.518006             -1.213881  ...   
61494         0.324113          0.124332             -1.287047  ...   
61568         0.296496          0.397012             -0.994168  ...   
61642         0.347591          0.179811             -1.491496  ...   
61716         0.366380          0.027494             -1.577043  ...   

       spectral_contrast5std  spectral_contrast5skew  \
0                        NaN                     NaN   
74                  2.087949                0.468411   
148                 2.639605                1.039552   
222                 3.572077                0.140919   
296                 4.424209                0.036302   
...                      ...                     ...   
61420               2.544686                0.121852   
61494               4.593361                0.448705   
61568               2.776943                0.127441   
61642               2.663166                0.560173   
61716               3.946151                0.225784   

       spectral_contrast5kurtosis  spectral_contrast6min  \
0                             NaN                    NaN   
74                       0.584898              10.197961   
148                      1.358847              12.225095   
222                     -0.726412              14.191255   
296                     -0.939122               9.195723   
...                           ...                    ...   
61420                   -0.175505              14.525187   
61494                   -0.977389              12.194958   
61568                   -0.509352              17.414860   
61642                    0.123